## Introduction

We seek to evaluate the integral

$$
I = \int_{0}^{2} \frac{1}{\sqrt{1 + \sin^2(x)}} \, dx
$$ {#eq-integral}

This integral does not have an elementary closed-form solution. It is an *elliptic integral*[^1]. Therefore, we must use numerical methods. We compare the **Trapezoidal rule** and **Gaussian quadrature** in terms of accuracy and computational efficiency.

[^1]: <https://en.wikipedia.org/wiki/Elliptic_integral>

In [1]:
#| label: setup
#| echo: false
#| output: false
import numpy as np
import matplotlib.pyplot as plt
from scipy import integrate
import time

def f(x):
    return 1 / np.sqrt(1 + np.sin(x)**2)

I_ref, _ = integrate.quad(f, 0, 2, limit=100)

## Numerical Methods

### Trapezoidal Rule

The composite trapezoidal rule approximates the integral as:

$$
I \approx \frac{h}{2}\left[f(a) + 2\sum_{i=1}^{n-1}f(x_i) + f(b)\right]
$$ {#eq-trapz}

where $h = (b-a)/n$ is the step size.

### Gaussian Quadrature

Gaussian quadrature uses optimally chosen nodes and weights:

$$
I \approx \sum_{i=1}^{n} w_i f(x_i)
$$ {#eq-gauss}

For smooth functions, Gaussian quadrature achieves much higher accuracy with fewer function evaluations, see e.g., @golubWelsch and @cenanovic.

In [2]:
#| label: fig-convergence
#| fig-cap: "Convergence comparison: error vs number of points for both methods."
#| echo: false

def trapezoidal(f, a, b, n): 
    x = np.linspace(a, b, n + 1)
    y = f(x)
    h = (b - a) / n
    return h * (0.5 * y[0] + np.sum(y[1:-1]) + 0.5 * y[-1])

def gauss_legendre(f, a, b, n):
    nodes, weights = np.polynomial.legendre.leggauss(n)
    x = 0.5 * (b - a) * nodes + 0.5 * (b + a)
    return 0.5 * (b - a) * np.sum(weights * f(x))

# Convergence study - cut at 25000 iterations
n_trap = np.unique(np.logspace(1, np.log10(25000), 50).astype(int))
n_gauss = np.arange(2, 40)

err_trap = [abs(trapezoidal(f, 0, 2, n) - I_ref) for n in n_trap]
err_gauss = [abs(gauss_legendre(f, 0, 2, n) - I_ref) for n in n_gauss]

plt.figure(figsize=(8, 5))
plt.loglog(n_trap, err_trap, 'b-o', label='Trapezoidal', markersize=4)
plt.loglog(n_gauss, err_gauss, 'r-s', label='Gauss-Legendre', markersize=4)
plt.axhline(1e-10, color='k', linestyle='--', label='Target: $10^{-10}$')
plt.xlabel('Number of points')
plt.ylabel('Absolute error')
plt.legend()
plt.grid(True, alpha=0.3, which='both')
plt.tight_layout()
plt.show()

<Figure size 2400x1500 with 1 Axes>

In [3]:
#| label: tbl-results
#| tbl-cap: "Points required and computation time to achieve error < $10^{-10}$."
#| echo: false

from IPython.display import Markdown

target = 1e-10
for n in range(10, 100000):
    if abs(trapezoidal(f, 0, 2, n) - I_ref) < target:
        n_trap_min = n
        break

for n in range(2, 100):
    if abs(gauss_legendre(f, 0, 2, n) - I_ref) < target:
        n_gauss_min = n
        break

t0 = time.perf_counter()
for _ in range(1000):
    trapezoidal(f, 0, 2, n_trap_min)
t_trap = (time.perf_counter() - t0) / 1000 * 1e6

t0 = time.perf_counter()
for _ in range(1000):
    gauss_legendre(f, 0, 2, n_gauss_min)
t_gauss = (time.perf_counter() - t0) / 1000 * 1e6

table = f"""
| Method | Points Required | Time (μs) |
|--------|-----------------|----------:|
| Trapezoidal | {n_trap_min} | {t_trap:.1f} |
| Gauss-Legendre | {n_gauss_min} | {t_gauss:.1f} |
"""
Markdown(table)


| Method | Points Required | Time (μs) |
|--------|-----------------|----------:|
| Trapezoidal | 22602 | 209.3 |
| Gauss-Legendre | 12 | 202.7 |


## Conclusion

Gaussian quadrature dramatically outperforms the trapezoidal rule for this smooth integrand. To achieve an error below $10^{-10}$, trapezoidal rule requires thousands of points whereas Gaussian rule requires only 12 points. See @fig-convergence for the convergence comparison and @tbl-results for the numerical results.

This demonstrates the power of Gaussian quadrature for smooth functions, where it achieves *exponential* convergence compared to the *algebraic* ($O(h^2)$) convergence of the trapezoidal rule.